In [1]:
!pip install tqdm
!pip install selenium
!pip install webdriver-manager

In [2]:
import requests
from bs4 import BeautifulSoup
from tqdm.notebook import tqdm
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.keys import Keys
import time

In [3]:
marking = False

In [13]:
marker_url = []

for i in range(6):
    marker_url.append(" ")

In [14]:
def ex_tag_selenium(sid, page, marker_url):
    driver = None  # 변수 초기화
    
    try:
        # Chrome WebDriver 설정
        chrome_options = Options()
        chrome_options.add_argument("--headless")
        driver = webdriver.Chrome(options=chrome_options)

        url = f"https://news.naver.com/main/main.naver?mode=LSD&mid=shm&sid1={sid}#&data=%2000:00:00&page={page}"

        # Selenium을 사용하여 페이지 열기
        driver.get(url)

        # WebDriverWait를 사용하여 특정 조건이 충족될 때까지 대기
        wait = WebDriverWait(driver, 20)  # 최대 20초간 대기
        a_tags = wait.until(EC.presence_of_all_elements_located((By.CSS_SELECTOR, '#section_body a')))

        
        tag_set = set()  # 중복을 방지하기 위한 집합(set)을 사용합니다.
        for a in a_tags:
            href = a.get_attribute('href')
            if href and f"sid={sid}" in href and "article" in href:
                tag_set.add(href)

        tag_lst = list(tag_set)
        
        # 특정 marker URL이 중복인지 확인
        if marker_url[sid-100] in tag_lst:
            print(f"Marker URL '{marker_url[sid-100]}'가 중복되었습니다. 작업을 종료합니다.")
            marking = True
            return tag_lst
        marking = False
        return tag_lst

    finally:
        # 웹 드라이버 종료
        if driver is not None:
            driver.quit()

In [15]:
result = ex_tag_selenium(sid=100, page=3, marker_url)
result
print(len(result))

SyntaxError: positional argument follows keyword argument (Temp/ipykernel_11380/208594755.py, line 1)

# 페이지 크롤링 - 공통된 세팅을 가지고 있는 네이버 뉴스의 포멧을 이용.
def ex_tag(sid, page):
    
    url = f"https://news.naver.com/main/main.naver?mode=LSD&mid=shm&sid1={sid}"\
    "#&data=%2000:00:00&page={page}"
    html = requests.get(url, headers={"User-Agent": "Mozilla/5.0"\
    "(Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko)"\
    "Chrome/110.0.0.0 Safari/537.36"})
    soup = BeautifulSoup(html.text, "html.parser")
    a_tag = soup.find_all("a", {'id':'section_body'})
    tag_lst = []
    for a in a_tag:
        if "href" in a.attrs:
            if(f"sid={sid}" in a["href"]) and ("article" in a["href"]):
                tag_lst.append(a["href"])
    return tag_lst

## 테스트
tag_lst = ex_tag(100, 2)
tag_lst

In [16]:
## 네이버 뉴스 분야별 뉴스 크롤링
def re_tag(sid):
    re_lst = []
    for i in tqdm(range(100)):
        lst = ex_tag_selenium(sid, i+1, marker_url)
        re_lst.extend(lst)
        if(marking == True):
            return re_lst
        
    ## 중복 제거
##    re_set = set(re_lst)
##    re_lst = list(re_set)
    
    return re_lst

In [17]:
## 범위
## 100 - 정치, 101 - 경제, 102 - 사회, 103 - 생활/문화, 104 - 세계, 105 -  IT/과학
all_hrefs = {}
sids = [i for i in range(100, 106)]

## URL을 이용해 뉴스 크롤링
for sid in sids:
    sid_data = re_tag(sid)
    all_hrefs[sid] = sid_data

  0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/100 [00:00<?, ?it/s]

In [18]:
all_hrefs

{100: ['https://n.news.naver.com/mnews/article/088/0000854688?sid=100',
  'https://n.news.naver.com/mnews/article/001/0014418102?sid=100',
  'https://n.news.naver.com/mnews/article/660/0000052552?sid=100',
  'https://n.news.naver.com/mnews/article/586/0000070359?sid=100',
  'https://n.news.naver.com/mnews/article/015/0004931281?sid=100',
  'https://n.news.naver.com/mnews/article/469/0000777950?sid=100',
  'https://n.news.naver.com/mnews/article/052/0001979176?sid=100',
  'https://n.news.naver.com/mnews/article/088/0000854691?sid=100',
  'https://n.news.naver.com/mnews/article/449/0000264837?sid=100',
  'https://n.news.naver.com/mnews/article/469/0000777946?sid=100',
  'https://n.news.naver.com/mnews/article/421/0007263275?sid=100',
  'https://n.news.naver.com/mnews/article/656/0000074629?sid=100',
  'https://n.news.naver.com/mnews/article/003/0012294314?sid=100',
  'https://n.news.naver.com/mnews/article/629/0000257698?sid=100',
  'https://n.news.naver.com/mnews/article/119/0002785054?

In [19]:
len(all_hrefs[105])

2000

In [20]:
## 각 기사에 내부 데이터 가져오기
## 제목, 날짜, 내용
def art_crawl(all_hrefs, sid, index):
    
    
    art_dic = {}
    
    title_selector = "#title_area > span"
    date_selector = "#ct > div.media_end_head.go_trans > div.media_end_head_info.nv_notrans"\
    "> div.media_end_head_info_datestamp > div:nth-child(1) > span"
    main_selector = "#dic_area"
    
    url = all_hrefs[sid][index]
    html = requests.get(url, headers = {"User-Agent": "Mozilla/5.0 "\
    "(Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko)"\
    "Chrome/110.0.0.0 Safari/537.36"})
    soup = BeautifulSoup(html.text, "lxml")
    
    ## 제목
    title = soup.select(title_selector)
    title_lst = [t.text for t in title]
    title_str = "".join(title_lst)
    
    ## 날짜
    date = soup.select(date_selector)
    date_lst = [d.text for d in date]
    date_str = "".join(date_lst)
    
    ## 내용
    main = soup.select(main_selector)
    main_lst = []
    for m in main:
        m_text = m.text
        ## 글자만 추출
        m_text = m_text.strip()
        main_lst.append(m_text)
    main_str = "".join(main_lst)
    
    
    art_dic["title"] = title_str
    art_dic["date"] = date_str
    art_dic["main"] = main_str
    
    return art_dic

In [21]:
section_lst = [s for s in range(100, 106)]
artdic_lst = []

## 실제로 크롤링을 하는 곳
for section in tqdm(section_lst):
    for i in tqdm(range(len(all_hrefs[section]))):
        art_dic = art_crawl(all_hrefs, section, i)
        art_dic["section"] = section
        art_dic["url"] = all_hrefs[section][i]
        artdic_lst.append(art_dic)

  0%|          | 0/6 [00:00<?, ?it/s]

  0%|          | 0/2000 [00:00<?, ?it/s]

  0%|          | 0/2000 [00:00<?, ?it/s]

  0%|          | 0/2000 [00:00<?, ?it/s]

  0%|          | 0/2000 [00:00<?, ?it/s]

  0%|          | 0/2000 [00:00<?, ?it/s]

  0%|          | 0/2000 [00:00<?, ?it/s]

In [22]:
artdic_lst

[{'title': '"대리기사 찾습니다" 보복 운전 논란 이경, 불법현수막 신고 당해',
  'date': '2023.12.31. 오후 12:50',
  'main': '자유대한호국단 "현수막 게시 불법" 관할 지자체에 신고\n\n\n\n이경 더불어민주당 전 상근부대변인. 연합뉴스보복 운전 혐의로 벌금형을 선고받은 이경 전 더불어민주당 상근부대변인이 무죄를 주장하며 대리운전기사를 찾기 위해 현수막을 내걸었다가 이러한 현수막 게시가 불법이라는 이유로 관할 지방자치단체에 신고 당했다.31일 한 온라인 커뮤니티에 따르면 자유대한호국단은 최근 서울 영등포구 여의도 국회의사당 부근에 걸린 이 전 부대변인이 게시한 현수막을 불법 현수막으로 신고했다며 유튜브 채널을 통해 문자 내역을 공개했다.\n\n\n\n보복 운전 혐의로 벌금형을 선고받은 이경 전 더불어민주당 상근부대변인이 무죄를 주장하며 대리운전기사를 찾기 위해 현수막을 내걸었다가 관할 지방자치단체에 신고 당했다. 온라인 커뮤니티 갈무리옥외광고물 등의 관리와 옥외광고산업 진흥에 관한 법률에 의거하면 단체나 개인의 적법한 정치활동을 위한 현수막은 지자체 신고·허가 등 설치에 제한이 없다.다만 정당의 정책이나 정치적 현안을 표시하는 경우에는 정당의 명칭, 정당의 연락처, 설치업체의 연락처, 현수막 표시 기간 등을 작성해야 한다.하지만 이 전 부대변인의 현수막에는 이 같은 정보가 빠져있고 휴대전화번호만 적혀 있다. 현수막에는 \'대리기사님을 찾습니다\', \'여의도에서 선유도역 또는 CU양평한신점으로 대리운전 해주신 기사님 연락 주십시오. 사례하겠습니다\' 등의 내용이 담겨 있다.신고자는 관할구역인 영등포구청에서 연락이 왔다며 담당 공무원이 이 전 부 대변인에게 불법 현수막 신고가 들어왔으니 오늘 중으로 자진 철거하지 않으면 강제 철거하고 과태료를 부과할 것을 예고했다고 밝혔다.앞서 이 전 부대변인은 지난 2021년 11월 12일 오후 10시쯤 서울 영등포구의 한 도로에서 운전하던 중 차선을 변경한 자신에게 뒤차가 경적을

In [23]:
artdic_lst[1].get('section')

def marking_date(all_hrefs):
    index = 0
    mark_date = []
    for section in section_lst:
        mark_date.append(artdic_lst[index].get('date'))
        index += len(all_hrefs[section])
    
    return mark_date

In [24]:
marking = marking_date(all_hrefs)

marking

['2023.12.31. 오후 12:50',
 '2023.12.31. 오후 2:34',
 '2023.12.31. 오후 3:28',
 '2023.12.31. 오후 4:14',
 '2023.12.31. 오후 3:11',
 '2023.12.31. 오후 3:11']

In [25]:
len(all_hrefs[105])

2000

In [26]:
all_hrefs[100]

['https://n.news.naver.com/mnews/article/088/0000854688?sid=100',
 'https://n.news.naver.com/mnews/article/001/0014418102?sid=100',
 'https://n.news.naver.com/mnews/article/660/0000052552?sid=100',
 'https://n.news.naver.com/mnews/article/586/0000070359?sid=100',
 'https://n.news.naver.com/mnews/article/015/0004931281?sid=100',
 'https://n.news.naver.com/mnews/article/469/0000777950?sid=100',
 'https://n.news.naver.com/mnews/article/052/0001979176?sid=100',
 'https://n.news.naver.com/mnews/article/088/0000854691?sid=100',
 'https://n.news.naver.com/mnews/article/449/0000264837?sid=100',
 'https://n.news.naver.com/mnews/article/469/0000777946?sid=100',
 'https://n.news.naver.com/mnews/article/421/0007263275?sid=100',
 'https://n.news.naver.com/mnews/article/656/0000074629?sid=100',
 'https://n.news.naver.com/mnews/article/003/0012294314?sid=100',
 'https://n.news.naver.com/mnews/article/629/0000257698?sid=100',
 'https://n.news.naver.com/mnews/article/119/0002785054?sid=100',
 'https://

In [27]:
all_hrefs[100][0]

'https://n.news.naver.com/mnews/article/088/0000854688?sid=100'

In [6]:
for i in range(6):
    marker_url[i] = all_hrefs[100+i][0]

NameError: name 'marker_url' is not defined

In [ ]:
marker_url